In [1]:
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')
from numpy import sqrt 

#Tien Xu Ly
from sklearn.preprocessing import MinMaxScaler

#Draw Flot
import matplotlib.pyplot as plt

#Cacuale error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score

#Dtw Libaray
from dtw import dtw

#FFNN Libarary
from keras.models import Sequential
from keras.layers import Dense
from keras.callbacks import EarlyStopping
from sklearn.model_selection import GridSearchCV
from keras.wrappers.scikit_learn import KerasRegressor

In [2]:
# Load dữ liệu
dataCSV = pd.read_csv('D:/DATN/Dataset/GE.csv')
dataCSV

Date      Open      High       Low     Close  Adj Close  \
0      1962-01-02  0.751202  0.763722  0.743690  0.748698   0.001782   
1      1962-01-03  0.744942  0.744942  0.738682  0.741186   0.001764   
2      1962-01-04  0.741186  0.747446  0.726162  0.732422   0.001743   
3      1962-01-05  0.732422  0.733674  0.701122  0.713642   0.001698   
4      1962-01-08  0.713642  0.713642  0.691106  0.712390   0.001695   
...           ...       ...       ...       ...       ...        ...   
14658  2020-03-26  7.630000  8.300000  7.510000  8.120000   8.120000   
14659  2020-03-27  7.680000  7.870000  7.540000  7.620000   7.620000   
14660  2020-03-30  7.540000  7.940000  7.350000  7.890000   7.890000   
14661  2020-03-31  7.870000  8.180000  7.820000  7.940000   7.940000   
14662  2020-04-01  7.520000  7.550000  7.000000  7.040000   7.040000   

          Volume  
0        2156500  
1        1477600  
2        1837000  
3        2725600  
4        3095000  
...          ...  
14658  123180900  
14659   93299000  
14660   86850200  
14661  121149900  
14662   99330200  

[14663 rows x 7 columns]

In [3]:
data_GE=dataCSV[['Close']]

In [4]:
# Replace null values with 0
data_GE.fillna(0, inplace=True)

# Remove outliers by replacing values outside of 3 standard deviations with the mean
std = data_GE['Close'].std()
mean = data_GE['Close'].mean()
data_GE['Close'] = np.where(data_GE['Close'] > (mean + 10*std), mean, data_GE['Close'])
data_GE['Close'] = np.where(data_GE['Close'] < (mean - 10*std), mean, data_GE['Close'])

# # Scale data_GE to range [0, 1]
scaler = MinMaxScaler()
data_GE['Close'] = scaler.fit_transform(data_GE['Close'].values.reshape(-1, 1))

# Fill in missing values with the mean of the previous and next values
data_GE['Close'] = data_GE['Close'].interpolate(method='linear')

# Print the cleaned data_GE
print(data_GE)

          Close
0      0.003375
1      0.003243
2      0.003090
3      0.002761
4      0.002739
...         ...
14658  0.132387
14659  0.123636
14660  0.128361
14661  0.129237
14662  0.113485

[14663 rows x 1 columns]


In [5]:
data = data_GE
# Chia dữ liệu thành train set và test set
train_size = int(len(data) * 0.8)
train_data = data.iloc[:train_size, :]
test_data = data.iloc[train_size:, :]

In [6]:
#Xử lý dữ liệu thành dữ liệu đầu vào và đầu ra cho mô hình
def prepare_data(data, size_window,size_predict,stepWindow):
    X, y = [], []
    startWindow = 0
    for i in range(len(data) - size_window - 1):
        if (len(data[(startWindow + size_window):(startWindow + size_window + size_predict) , 0]) != size_predict):
            break
        X.append(data[startWindow:(startWindow + size_window), :])
        y.append(data[(startWindow + size_window):(startWindow + size_window + size_predict) , 0])
        print(data[startWindow:(startWindow + size_window), :])
        print("-----")
        print(data[(startWindow + size_window):(startWindow + size_window + size_predict) , 0])     
       
        startWindow += stepWindow
    return np.array(X), np.array(y)

size_window = 20
size_predict=1
stepWindow=1
X_train, y_train = prepare_data(train_data.values, size_window, size_predict, stepWindow)
X_test, y_test = prepare_data(test_data.values, size_window, size_predict, stepWindow)

[[0.00337453]
 [0.00324305]
 [0.00308967]
 [0.00276098]
 [0.00273907]
 [0.0028048 ]
 [0.00287054]
 [0.00289245]
 [0.00271715]
 [0.00284863]
 [0.00295819]
 [0.00267333]
 [0.0028048 ]
 [0.00291437]
 [0.00295819]
 [0.00271715]
 [0.00295819]
 [0.00282672]
 [0.00278289]
 [0.0028048 ]]
-----
[0.00302393]
[[0.00324305]
 [0.00308967]
 [0.00276098]
 [0.00273907]
 [0.0028048 ]
 [0.00287054]
 [0.00289245]
 [0.00271715]
 [0.00284863]
 [0.00295819]
 [0.00267333]
 [0.0028048 ]
 [0.00291437]
 [0.00295819]
 [0.00271715]
 [0.00295819]
 [0.00282672]
 [0.00278289]
 [0.0028048 ]
 [0.00302393]]
-----
[0.00341835]
[[0.00308967]
 [0.00276098]
 [0.00273907]
 [0.0028048 ]
 [0.00287054]
 [0.00289245]
 [0.00271715]
 [0.00284863]
 [0.00295819]
 [0.00267333]
 [0.0028048 ]
 [0.00291437]
 [0.00295819]
 [0.00271715]
 [0.00295819]
 [0.00282672]
 [0.00278289]
 [0.0028048 ]
 [0.00302393]
 [0.00341835]]
-----
[0.0033307]
[[0.00276098]
 [0.00273907]
 [0.0028048 ]
 [0.00287054]
 [0.00289245]
 [0.00271715]
 [0.00284863]
 [0

[[0.00308967]
 [0.00317732]
 [0.00293628]
 [0.00300202]
 [0.00308967]
 [0.00306775]
 [0.00311158]
 [0.00311158]
 [0.00319923]
 [0.00322114]
 [0.0033307 ]
 [0.00335262]
 [0.0033307 ]
 [0.00308967]
 [0.0033307 ]
 [0.00337453]
 [0.00372513]
 [0.00372513]
 [0.0036813 ]
 [0.0036813 ]]
-----
[0.00359365]
[[0.00317732]
 [0.00293628]
 [0.00300202]
 [0.00308967]
 [0.00306775]
 [0.00311158]
 [0.00311158]
 [0.00319923]
 [0.00322114]
 [0.0033307 ]
 [0.00335262]
 [0.0033307 ]
 [0.00308967]
 [0.0033307 ]
 [0.00337453]
 [0.00372513]
 [0.00372513]
 [0.0036813 ]
 [0.0036813 ]
 [0.00359365]]
-----
[0.00381278]
[[0.00293628]
 [0.00300202]
 [0.00308967]
 [0.00306775]
 [0.00311158]
 [0.00311158]
 [0.00319923]
 [0.00322114]
 [0.0033307 ]
 [0.00335262]
 [0.0033307 ]
 [0.00308967]
 [0.0033307 ]
 [0.00337453]
 [0.00372513]
 [0.00372513]
 [0.0036813 ]
 [0.0036813 ]
 [0.00359365]
 [0.00381278]]
-----
[0.00387852]
[[0.00300202]
 [0.00308967]
 [0.00306775]
 [0.00311158]
 [0.00311158]
 [0.00319923]
 [0.00322114]
 [

[[0.00883075]
 [0.00885266]
 [0.00889648]
 [0.00885266]
 [0.00854588]
 [0.00861162]
 [0.00858971]
 [0.00832676]
 [0.00832676]
 [0.00799807]
 [0.00810763]
 [0.00815146]
 [0.00819528]
 [0.0083925 ]
 [0.00828294]
 [0.0080419 ]
 [0.00791042]
 [0.00788851]
 [0.00799807]
 [0.00766938]]
-----
[0.0073407]
[[0.00885266]
 [0.00889648]
 [0.00885266]
 [0.00854588]
 [0.00861162]
 [0.00858971]
 [0.00832676]
 [0.00832676]
 [0.00799807]
 [0.00810763]
 [0.00815146]
 [0.00819528]
 [0.0083925 ]
 [0.00828294]
 [0.0080419 ]
 [0.00791042]
 [0.00788851]
 [0.00799807]
 [0.00766938]
 [0.0073407 ]]
-----
[0.00709966]
[[0.00889648]
 [0.00885266]
 [0.00854588]
 [0.00861162]
 [0.00858971]
 [0.00832676]
 [0.00832676]
 [0.00799807]
 [0.00810763]
 [0.00815146]
 [0.00819528]
 [0.0083925 ]
 [0.00828294]
 [0.0080419 ]
 [0.00791042]
 [0.00788851]
 [0.00799807]
 [0.00766938]
 [0.0073407 ]
 [0.00709966]]
-----
[0.00720922]
[[0.00885266]
 [0.00854588]
 [0.00861162]
 [0.00858971]
 [0.00832676]
 [0.00832676]
 [0.00799807]
 [0

[0.00495223]
[[0.00670523]
 [0.00609168]
 [0.00604786]
 [0.00591638]
 [0.00569726]
 [0.00521518]
 [0.00543431]
 [0.00587256]
 [0.00567534]
 [0.00545622]
 [0.00517136]
 [0.00532474]
 [0.00517136]
 [0.00530283]
 [0.00503988]
 [0.00495223]
 [0.00464546]
 [0.00455781]
 [0.00447016]
 [0.00495223]]
-----
[0.00497414]
[[0.00609168]
 [0.00604786]
 [0.00591638]
 [0.00569726]
 [0.00521518]
 [0.00543431]
 [0.00587256]
 [0.00567534]
 [0.00545622]
 [0.00517136]
 [0.00532474]
 [0.00517136]
 [0.00530283]
 [0.00503988]
 [0.00495223]
 [0.00464546]
 [0.00455781]
 [0.00447016]
 [0.00495223]
 [0.00497414]]
-----
[0.00565343]
[[0.00604786]
 [0.00591638]
 [0.00569726]
 [0.00521518]
 [0.00543431]
 [0.00587256]
 [0.00567534]
 [0.00545622]
 [0.00517136]
 [0.00532474]
 [0.00517136]
 [0.00530283]
 [0.00503988]
 [0.00495223]
 [0.00464546]
 [0.00455781]
 [0.00447016]
 [0.00495223]
 [0.00497414]
 [0.00565343]]
-----
[0.00587256]
[[0.00591638]
 [0.00569726]
 [0.00521518]
 [0.00543431]
 [0.00587256]
 [0.00567534]
 [0

[[0.00694627]
 [0.00707775]
 [0.00692436]
 [0.0069901 ]
 [0.00718731]
 [0.00729687]
 [0.00725305]
 [0.00727496]
 [0.00705583]
 [0.00709966]
 [0.00718731]
 [0.00749408]
 [0.00731878]
 [0.00738452]
 [0.00727496]
 [0.0073407 ]
 [0.00736261]
 [0.00720922]
 [0.00736261]
 [0.00727496]]
-----
[0.00731878]
[[0.00707775]
 [0.00692436]
 [0.0069901 ]
 [0.00718731]
 [0.00729687]
 [0.00725305]
 [0.00727496]
 [0.00705583]
 [0.00709966]
 [0.00718731]
 [0.00749408]
 [0.00731878]
 [0.00738452]
 [0.00727496]
 [0.0073407 ]
 [0.00736261]
 [0.00720922]
 [0.00736261]
 [0.00727496]
 [0.00731878]]
-----
[0.0076913]
[[0.00692436]
 [0.0069901 ]
 [0.00718731]
 [0.00729687]
 [0.00725305]
 [0.00727496]
 [0.00705583]
 [0.00709966]
 [0.00718731]
 [0.00749408]
 [0.00731878]
 [0.00738452]
 [0.00727496]
 [0.0073407 ]
 [0.00736261]
 [0.00720922]
 [0.00736261]
 [0.00727496]
 [0.00731878]
 [0.0076913 ]]
-----
[0.00745026]
[[0.0069901 ]
 [0.00718731]
 [0.00729687]
 [0.00725305]
 [0.00727496]
 [0.00705583]
 [0.00709966]
 [0

...

[[0.4029135 ]
 [0.4101499 ]
 [0.4141888 ]
 [0.41183277]
 [0.41822773]
 [0.41755457]
 [0.41839601]
 [0.42344466]
 [0.42193007]
 [0.41772285]
 [0.4130108 ]
 [0.40998162]
 [0.4158717 ]
 [0.41553511]
 [0.41603998]
 [0.41940573]
 [0.41890088]
 [0.4130108 ]
 [0.42193007]
 [0.42664212]]
-----
[0.43152249]
[[0.4101499 ]
 [0.4141888 ]
 [0.41183277]
 [0.41822773]
 [0.41755457]
 [0.41839601]
 [0.42344466]
 [0.42193007]
 [0.41772285]
 [0.4130108 ]
 [0.40998162]
 [0.4158717 ]
 [0.41553511]
 [0.41603998]
 [0.41940573]
 [0.41890088]
 [0.4130108 ]
 [0.42193007]
 [0.42664212]
 [0.43152249]]
-----
[0.4300079]
[[0.4141888 ]
 [0.41183277]
 [0.41822773]
 [0.41755457]
 [0.41839601]
 [0.42344466]
 [0.42193007]
 [0.41772285]
 [0.4130108 ]
 [0.40998162]
 [0.4158717 ]
 [0.41553511]
 [0.41603998]
 [0.41940573]
 [0.41890088]
 [0.4130108 ]
 [0.42193007]
 [0.42664212]
 [0.43152249]
 [0.4300079 ]]
-----
[0.42849331]
[[0.41183277]
 [0.41822773]
 [0.41755457]
 [0.41839601]
 [0.42344466]
 [0.42193007]
 [0.41772285]
 [0

[[0.41620826]
 [0.42176179]
 [0.41654486]
 [0.41772285]
 [0.41890088]
 [0.41553511]
 [0.40947674]
 [0.40762556]
 [0.40863531]
 [0.4130108 ]
 [0.40779387]
 [0.40829871]
 [0.40998162]
 [0.41402052]
 [0.41132789]
 [0.41115961]
 [0.42327638]
 [0.47006049]
 [0.45525114]
 [0.45693401]]
-----
[0.45239024]
[[0.42176179]
 [0.41654486]
 [0.41772285]
 [0.41890088]
 [0.41553511]
 [0.40947674]
 [0.40762556]
 [0.40863531]
 [0.4130108 ]
 [0.40779387]
 [0.40829871]
 [0.40998162]
 [0.41402052]
 [0.41132789]
 [0.41115961]
 [0.42327638]
 [0.47006049]
 [0.45525114]
 [0.45693401]
 [0.45239024]]
-----
[0.44936106]
[[0.41654486]
 [0.41772285]
 [0.41890088]
 [0.41553511]
 [0.40947674]
 [0.40762556]
 [0.40863531]
 [0.4130108 ]
 [0.40779387]
 [0.40829871]
 [0.40998162]
 [0.41402052]
 [0.41132789]
 [0.41115961]
 [0.42327638]
 [0.47006049]
 [0.45525114]
 [0.45693401]
 [0.45239024]
 [0.44936106]]
-----
[0.44885618]
[[0.41772285]
 [0.41890088]
 [0.41553511]
 [0.40947674]
 [0.40762556]
 [0.40863531]
 [0.4130108 ]
 [

[0.5298028]
[[0.49210624]
 [0.48369184]
 [0.4941257 ]
 [0.50439128]
 [0.52004207]
 [0.52021038]
 [0.51953723]
 [0.52441756]
 [0.52576387]
 [0.53215883]
 [0.53232711]
 [0.53316855]
 [0.53485145]
 [0.53939523]
 [0.54360244]
 [0.54410728]
 [0.54444387]
 [0.54191953]
 [0.53872207]
 [0.5298028 ]]
-----
[0.52273469]
[[0.48369184]
 [0.4941257 ]
 [0.50439128]
 [0.52004207]
 [0.52021038]
 [0.51953723]
 [0.52441756]
 [0.52576387]
 [0.53215883]
 [0.53232711]
 [0.53316855]
 [0.53485145]
 [0.53939523]
 [0.54360244]
 [0.54410728]
 [0.54444387]
 [0.54191953]
 [0.53872207]
 [0.5298028 ]
 [0.52273469]]
-----
[0.51987379]
[[0.4941257 ]
 [0.50439128]
 [0.52004207]
 [0.52021038]
 [0.51953723]
 [0.52441756]
 [0.52576387]
 [0.53215883]
 [0.53232711]
 [0.53316855]
 [0.53485145]
 [0.53939523]
 [0.54360244]
 [0.54410728]
 [0.54444387]
 [0.54191953]
 [0.53872207]
 [0.5298028 ]
 [0.52273469]
 [0.51987379]]
-----
[0.51667632]
[[0.50439128]
 [0.52004207]
 [0.52021038]
 [0.51953723]
 [0.52441756]
 [0.52576387]
 [0.

[[0.28830925]
 [0.28830925]
 [0.2872995 ]
 [0.29167499]
 [0.28915068]
 [0.28713122]
 [0.2901604 ]
 [0.28915068]
 [0.28628978]
 [0.28393375]
 [0.28427031]
 [0.28477519]
 [0.28359716]
 [0.28275572]
 [0.28241916]
 [0.28393375]
 [0.29285302]
 [0.29571392]
 [0.30210888]
 [0.30227716]]
-----
[0.29790167]
[[0.28830925]
 [0.2872995 ]
 [0.29167499]
 [0.28915068]
 [0.28713122]
 [0.2901604 ]
 [0.28915068]
 [0.28628978]
 [0.28393375]
 [0.28427031]
 [0.28477519]
 [0.28359716]
 [0.28275572]
 [0.28241916]
 [0.28393375]
 [0.29285302]
 [0.29571392]
 [0.30210888]
 [0.30227716]
 [0.29790167]]
-----
[0.30261372]
[[0.2872995 ]
 [0.29167499]
 [0.28915068]
 [0.28713122]
 [0.2901604 ]
 [0.28915068]
 [0.28628978]
 [0.28393375]
 [0.28427031]
 [0.28477519]
 [0.28359716]
 [0.28275572]
 [0.28241916]
 [0.28393375]
 [0.29285302]
 [0.29571392]
 [0.30210888]
 [0.30227716]
 [0.29790167]
 [0.30261372]]
-----
[0.3088404]
[[0.29167499]
 [0.28915068]
 [0.28713122]
 [0.2901604 ]
 [0.28915068]
 [0.28628978]
 [0.28393375]
 [0

[[0.15601452]
 [0.15548945]
 [0.15706463]
 [0.16529056]
 [0.16336535]
 [0.16389041]
 [0.16494052]
 [0.16616567]
 [0.1673908 ]
 [0.17019111]
 [0.17071618]
 [0.16931601]
 [0.16616567]
 [0.17264139]
 [0.17124124]
 [0.17631681]
 [0.1736915 ]
 [0.17019111]
 [0.169141  ]
 [0.1700161 ]]
-----
[0.17229135]
[[0.15548945]
 [0.15706463]
 [0.16529056]
 [0.16336535]
 [0.16389041]
 [0.16494052]
 [0.16616567]
 [0.1673908 ]
 [0.17019111]
 [0.17071618]
 [0.16931601]
 [0.16616567]
 [0.17264139]
 [0.17124124]
 [0.17631681]
 [0.1736915 ]
 [0.17019111]
 [0.169141  ]
 [0.1700161 ]
 [0.17229135]]
-----
[0.17404155]
[[0.15706463]
 [0.16529056]
 [0.16336535]
 [0.16389041]
 [0.16494052]
 [0.16616567]
 [0.1673908 ]
 [0.17019111]
 [0.17071618]
 [0.16931601]
 [0.16616567]
 [0.17264139]
 [0.17124124]
 [0.17631681]
 [0.1736915 ]
 [0.17019111]
 [0.169141  ]
 [0.1700161 ]
 [0.17229135]
 [0.17404155]]
-----
[0.17631681]
[[0.16529056]
 [0.16336535]
 [0.16389041]
 [0.16494052]
 [0.16616567]
 [0.1673908 ]
 [0.17019111]
 [

In [7]:
#define the grid search parameters
batch_size_FFNN = [8, 16, 32, 64, 128]
epochs_FFNN = [50, 100, 150, 200, 250, 300, 350, 400]
param_grid_FFNN = dict(batch_size=batch_size_FFNN, epochs=epochs_FFNN)

In [8]:
# create the model
def create_model_FFNN():
    model_FFNN = Sequential()
    model_FFNN.add(Dense(neural, input_dim=size_window, activation='sigmoid'))
    model_FFNN.add(Dense(1))
    model_FFNN.compile(loss='mean_squared_error', optimizer='adam')
    return model_FFNN

In [ ]:
df_MseWith_Neural = pd.DataFrame([],  columns =  ["Neural","Batch_Size","Epoch", "MSE"])
for neural in range(3,21):
    # create the model
    model_FFNN = KerasRegressor(build_fn=create_model_FFNN, verbose=0)
    # perform the grid search
    grid_FFNN = GridSearchCV(estimator=model_FFNN, param_grid=param_grid_FFNN, cv=3)
    grid_result_FFNN = grid_FFNN.fit(X_train, y_train)
    # train the model with the best parameters
    best_params_FFNN = grid_result_FFNN.best_params_
    model_FFNN = create_model_FFNN()
    model_FFNN.fit(X_train, y_train, epochs=best_params_FFNN['epochs'], batch_size=best_params_FFNN['batch_size'], verbose=2, callbacks=[EarlyStopping(monitor='loss', patience=10)], shuffle=False)
    # make predictions on the test set
    predictions_FFNN = model_FFNN.predict(X_test)
    # get the best weights from the model
    model_FFNN.save_weights('bestWeight/GE_best_weights/best_weights_FFNN_'+str(neural)+'_Neural_'+str(best_params_FFNN['batch_size'])+'_BatchSize_'+str(best_params_FFNN['epochs'])+'_Epoch_GE.h5')    
    # create the model
    model_FFNN1 = Sequential()
    model_FFNN1.add(Dense(neural, input_dim=size_window, activation='sigmoid'))
    model_FFNN1.add(Dense(1))
    model_FFNN1.load_weights('bestWeight/GE_best_weights/best_weights_FFNN_'+str(neural)+'_Neural_'+str(best_params_FFNN['batch_size'])+'_BatchSize_'+str(best_params_FFNN['epochs'])+'_Epoch_GE.h5')
    model_FFNN1.compile(loss='mean_squared_error', optimizer='adam')
    y_pred= model_FFNN1.predict(X_test)
    np.savetxt('predict/GE/predict_FFNN_'+str(neural)+'_Neural_'+str(best_params_FFNN['batch_size'])+'_BatchSize_'+str(best_params_FFNN['epochs'])+'_Epoch_GE.txt', y_pred)
    rowMseWithNeural = pd.Series([neural,best_params_FFNN['batch_size'],best_params_FFNN['epochs'], mean_squared_error(y_test , y_pred)], index=df_MseWith_Neural.columns)
    df_MseWith_Neural = df_MseWith_Neural.append(rowMseWithNeural,ignore_index=True)

Epoch 1/350
732/732 - 2s - loss: 0.0279 - 2s/epoch - 2ms/step
Epoch 2/350
732/732 - 1s - loss: 0.0092 - 948ms/epoch - 1ms/step
Epoch 3/350
732/732 - 1s - loss: 0.0062 - 950ms/epoch - 1ms/step
Epoch 4/350
732/732 - 1s - loss: 0.0047 - 980ms/epoch - 1ms/step
Epoch 5/350
732/732 - 1s - loss: 0.0035 - 944ms/epoch - 1ms/step
Epoch 6/350
732/732 - 1s - loss: 0.0027 - 949ms/epoch - 1ms/step
Epoch 7/350
732/732 - 1s - loss: 0.0021 - 958ms/epoch - 1ms/step
Epoch 8/350
732/732 - 1s - loss: 0.0017 - 973ms/epoch - 1ms/step
Epoch 9/350
732/732 - 1s - loss: 0.0014 - 958ms/epoch - 1ms/step
Epoch 10/350
732/732 - 1s - loss: 0.0012 - 959ms/epoch - 1ms/step
Epoch 11/350
732/732 - 1s - loss: 0.0011 - 949ms/epoch - 1ms/step
Epoch 12/350
732/732 - 1s - loss: 9.9153e-04 - 1s/epoch - 1ms/step
Epoch 13/350
732/732 - 1s - loss: 9.1897e-04 - 966ms/epoch - 1ms/step
Epoch 14/350
732/732 - 1s - loss: 8.6465e-04 - 949ms/epoch - 1ms/step
Epoch 15/350
732/732 - 1s - loss: 8.2342e-04 - 946ms/epoch - 1ms/step
Epoch 16/

Epoch 119/350
732/732 - 1s - loss: 4.7440e-04 - 944ms/epoch - 1ms/step
Epoch 120/350
732/732 - 1s - loss: 4.7352e-04 - 961ms/epoch - 1ms/step
Epoch 121/350
732/732 - 1s - loss: 4.7265e-04 - 937ms/epoch - 1ms/step
Epoch 122/350
732/732 - 1s - loss: 4.7180e-04 - 942ms/epoch - 1ms/step
Epoch 123/350
732/732 - 1s - loss: 4.7097e-04 - 961ms/epoch - 1ms/step
Epoch 124/350
732/732 - 1s - loss: 4.7014e-04 - 940ms/epoch - 1ms/step
Epoch 125/350
732/732 - 1s - loss: 4.6933e-04 - 969ms/epoch - 1ms/step
Epoch 126/350
732/732 - 1s - loss: 4.6853e-04 - 955ms/epoch - 1ms/step
Epoch 127/350
732/732 - 1s - loss: 4.6775e-04 - 950ms/epoch - 1ms/step
Epoch 128/350
732/732 - 1s - loss: 4.6697e-04 - 958ms/epoch - 1ms/step
Epoch 129/350
732/732 - 1s - loss: 4.6621e-04 - 966ms/epoch - 1ms/step
Epoch 130/350
732/732 - 1s - loss: 4.6545e-04 - 947ms/epoch - 1ms/step
Epoch 131/350
732/732 - 1s - loss: 4.6471e-04 - 938ms/epoch - 1ms/step
Epoch 132/350
732/732 - 1s - loss: 4.6399e-04 - 941ms/epoch - 1ms/step
Epoch 

Epoch 235/350
732/732 - 1s - loss: 4.2253e-04 - 959ms/epoch - 1ms/step
Epoch 236/350
732/732 - 1s - loss: 4.2228e-04 - 962ms/epoch - 1ms/step
Epoch 237/350
732/732 - 1s - loss: 4.2203e-04 - 938ms/epoch - 1ms/step
Epoch 238/350
732/732 - 1s - loss: 4.2179e-04 - 964ms/epoch - 1ms/step
Epoch 239/350
732/732 - 1s - loss: 4.2155e-04 - 943ms/epoch - 1ms/step
Epoch 240/350
732/732 - 1s - loss: 4.2131e-04 - 959ms/epoch - 1ms/step
Epoch 241/350
732/732 - 1s - loss: 4.2107e-04 - 953ms/epoch - 1ms/step
Epoch 242/350
732/732 - 1s - loss: 4.2084e-04 - 957ms/epoch - 1ms/step
Epoch 243/350
732/732 - 1s - loss: 4.2061e-04 - 954ms/epoch - 1ms/step
Epoch 244/350
732/732 - 1s - loss: 4.2037e-04 - 964ms/epoch - 1ms/step
Epoch 245/350
732/732 - 1s - loss: 4.2014e-04 - 945ms/epoch - 1ms/step
Epoch 246/350
732/732 - 1s - loss: 4.1991e-04 - 954ms/epoch - 1ms/step
Epoch 247/350
732/732 - 1s - loss: 4.1968e-04 - 940ms/epoch - 1ms/step
Epoch 248/350
732/732 - 1s - loss: 4.1946e-04 - 956ms/epoch - 1ms/step
Epoch 

91/91 [==============================] - 0s 1ms/step
Epoch 1/250
732/732 - 2s - loss: 0.0398 - 2s/epoch - 2ms/step
Epoch 2/250
732/732 - 1s - loss: 0.0021 - 1s/epoch - 1ms/step
Epoch 3/250
732/732 - 1s - loss: 0.0017 - 993ms/epoch - 1ms/step
Epoch 4/250
732/732 - 1s - loss: 0.0015 - 979ms/epoch - 1ms/step
Epoch 5/250
732/732 - 1s - loss: 0.0014 - 1s/epoch - 1ms/step
Epoch 6/250
732/732 - 1s - loss: 0.0013 - 996ms/epoch - 1ms/step
Epoch 7/250
732/732 - 1s - loss: 0.0012 - 994ms/epoch - 1ms/step
Epoch 8/250
732/732 - 1s - loss: 0.0012 - 970ms/epoch - 1ms/step
Epoch 9/250
732/732 - 1s - loss: 0.0011 - 984ms/epoch - 1ms/step
Epoch 10/250
732/732 - 1s - loss: 0.0011 - 989ms/epoch - 1ms/step
Epoch 11/250
732/732 - 1s - loss: 0.0011 - 986ms/epoch - 1ms/step
Epoch 12/250
732/732 - 1s - loss: 0.0010 - 995ms/epoch - 1ms/step
Epoch 13/250
732/732 - 1s - loss: 0.0010 - 981ms/epoch - 1ms/step
Epoch 14/250
732/732 - 1s - loss: 0.0010 - 1s/epoch - 1ms/step
Epoch 15/250
732/732 - 1s - loss: 9.9117e-04

Epoch 119/250
732/732 - 1s - loss: 6.1597e-04 - 1s/epoch - 1ms/step
Epoch 120/250
732/732 - 1s - loss: 6.1410e-04 - 974ms/epoch - 1ms/step
Epoch 121/250
732/732 - 1s - loss: 6.1224e-04 - 1s/epoch - 1ms/step
Epoch 122/250
732/732 - 1s - loss: 6.1040e-04 - 1s/epoch - 1ms/step
Epoch 123/250
732/732 - 1s - loss: 6.0857e-04 - 985ms/epoch - 1ms/step
Epoch 124/250
732/732 - 1s - loss: 6.0675e-04 - 1s/epoch - 1ms/step
Epoch 125/250
732/732 - 1s - loss: 6.0495e-04 - 988ms/epoch - 1ms/step
Epoch 126/250
732/732 - 1s - loss: 6.0316e-04 - 989ms/epoch - 1ms/step
Epoch 127/250
732/732 - 1s - loss: 6.0139e-04 - 991ms/epoch - 1ms/step
Epoch 128/250
732/732 - 1s - loss: 5.9963e-04 - 1s/epoch - 1ms/step
Epoch 129/250
732/732 - 1s - loss: 5.9788e-04 - 988ms/epoch - 1ms/step
Epoch 130/250
732/732 - 1s - loss: 5.9614e-04 - 980ms/epoch - 1ms/step
Epoch 131/250
732/732 - 1s - loss: 5.9441e-04 - 993ms/epoch - 1ms/step
Epoch 132/250
732/732 - 1s - loss: 5.9270e-04 - 976ms/epoch - 1ms/step
Epoch 133/250
732/732

Epoch 237/250
732/732 - 1s - loss: 4.4873e-04 - 993ms/epoch - 1ms/step
Epoch 238/250
732/732 - 1s - loss: 4.4753e-04 - 977ms/epoch - 1ms/step
Epoch 239/250
732/732 - 1s - loss: 4.4632e-04 - 1s/epoch - 1ms/step
Epoch 240/250
732/732 - 1s - loss: 4.4511e-04 - 975ms/epoch - 1ms/step
Epoch 241/250
732/732 - 1s - loss: 4.4391e-04 - 1s/epoch - 1ms/step
Epoch 242/250
732/732 - 1s - loss: 4.4271e-04 - 997ms/epoch - 1ms/step
Epoch 243/250
732/732 - 1s - loss: 4.4152e-04 - 998ms/epoch - 1ms/step
Epoch 244/250
732/732 - 1s - loss: 4.4033e-04 - 988ms/epoch - 1ms/step
Epoch 245/250
732/732 - 1s - loss: 4.3914e-04 - 972ms/epoch - 1ms/step
Epoch 246/250
732/732 - 1s - loss: 4.3795e-04 - 986ms/epoch - 1ms/step
Epoch 247/250
732/732 - 1s - loss: 4.3676e-04 - 992ms/epoch - 1ms/step
Epoch 248/250
732/732 - 1s - loss: 4.3558e-04 - 1s/epoch - 1ms/step
Epoch 249/250
732/732 - 1s - loss: 4.3441e-04 - 1s/epoch - 1ms/step
Epoch 250/250
732/732 - 1s - loss: 4.3323e-04 - 987ms/epoch - 1ms/step
91/91 [===========

183/183 - 0s - loss: 2.8577e-04 - 200ms/epoch - 1ms/step
Epoch 105/150
183/183 - 0s - loss: 2.8174e-04 - 199ms/epoch - 1ms/step
Epoch 106/150
183/183 - 0s - loss: 2.7782e-04 - 194ms/epoch - 1ms/step
Epoch 107/150
183/183 - 0s - loss: 2.7402e-04 - 213ms/epoch - 1ms/step
Epoch 108/150
183/183 - 0s - loss: 2.7035e-04 - 193ms/epoch - 1ms/step
Epoch 109/150
183/183 - 0s - loss: 2.6680e-04 - 211ms/epoch - 1ms/step
Epoch 110/150
183/183 - 0s - loss: 2.6337e-04 - 185ms/epoch - 1ms/step
Epoch 111/150
183/183 - 0s - loss: 2.6008e-04 - 198ms/epoch - 1ms/step
Epoch 112/150
183/183 - 0s - loss: 2.5693e-04 - 202ms/epoch - 1ms/step
Epoch 113/150
183/183 - 0s - loss: 2.5390e-04 - 191ms/epoch - 1ms/step
Epoch 114/150
183/183 - 0s - loss: 2.5101e-04 - 212ms/epoch - 1ms/step
Epoch 115/150
183/183 - 0s - loss: 2.4826e-04 - 186ms/epoch - 1ms/step
Epoch 116/150
183/183 - 0s - loss: 2.4563e-04 - 197ms/epoch - 1ms/step
Epoch 117/150
183/183 - 0s - loss: 2.4314e-04 - 214ms/epoch - 1ms/step
Epoch 118/150
183/18

Epoch 56/400
183/183 - 0s - loss: 2.9555e-04 - 211ms/epoch - 1ms/step
Epoch 57/400
183/183 - 0s - loss: 2.9210e-04 - 274ms/epoch - 1ms/step
Epoch 58/400
183/183 - 0s - loss: 2.8809e-04 - 227ms/epoch - 1ms/step
Epoch 59/400
183/183 - 0s - loss: 2.8361e-04 - 216ms/epoch - 1ms/step
Epoch 60/400
183/183 - 0s - loss: 2.7879e-04 - 204ms/epoch - 1ms/step
Epoch 61/400
183/183 - 0s - loss: 2.7382e-04 - 229ms/epoch - 1ms/step
Epoch 62/400
183/183 - 0s - loss: 2.6893e-04 - 216ms/epoch - 1ms/step
Epoch 63/400
183/183 - 0s - loss: 2.6436e-04 - 223ms/epoch - 1ms/step
Epoch 64/400
183/183 - 0s - loss: 2.6035e-04 - 217ms/epoch - 1ms/step
Epoch 65/400
183/183 - 0s - loss: 2.5710e-04 - 221ms/epoch - 1ms/step
Epoch 66/400
183/183 - 0s - loss: 2.5478e-04 - 228ms/epoch - 1ms/step
Epoch 67/400
183/183 - 0s - loss: 2.5350e-04 - 216ms/epoch - 1ms/step
Epoch 68/400
183/183 - 0s - loss: 2.5334e-04 - 213ms/epoch - 1ms/step
Epoch 69/400
183/183 - 0s - loss: 2.5423e-04 - 201ms/epoch - 1ms/step
Epoch 70/400
183/183

In [ ]:
df_MseWith_Neural

In [ ]:
# Vẽ biểu đồ
plt.plot(df_MseWith_Neural['MSE'], label='MSE')
plt.legend()
plt.show()

In [ ]:
df_MseWith_Neural_Sort = df_MseWith_Neural.sort_values('MSE')
best_Neural=df_MseWith_Neural['Neural'].iloc[0]   

In [ ]:
df_MseWith_Neural_Sort

In [ ]:
best_Neural